In [33]:
# from selenium import webdriver
# from selenium.webdriver.chrome.service import Service as ChromeService
# from webdriver_manager.chrome import ChromeDriverManager
# from selenium.webdriver.common.by import By
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup as bs
import requests
import re
import statsmodels.api as sm

In [2]:
year = 2022
week = 9
url = f'https://www.cbssports.com/college-football/scoreboard/FBS/{year}/regular/{week}/'

In [3]:
page = requests.get(url)
soup = bs(page.content)
soup

<!DOCTYPE html>
<html class="" lang="en" xmlns:fb="http://ogp.me/ns/fb#" xmlns:og="http://opengraphprotocol.org/schema/">
<head>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
<meta content="IE=edge,chrome=1" http-equiv="X-UA-Compatible"/>
<meta content="en" http-equiv="Content-Language"/>
<meta content="notranslate" name="google"/>
<link href="https://sportshub.cbsistatic.com" rel="preconnect dns-prefetch"/>
<link href="https://sportsfly.cbsistatic.com" rel="preconnect dns-prefetch"/>
<link href="https://sports.cbsimg.net" rel="preconnect dns-prefetch"/>
<title>2022 NCAA Football Scores - FBS - Week 9 - CBSSports.com</title>
<meta content="2022 NCAA Football Scores - FBS - Week 9 - CBSSports.com" itemprop="name"/>
<meta content="Live college football scores and postgame recaps." name="description"/>
<meta content="Live college football scores and postgame recaps." itemprop="description"/>
<link href="https://www.cbssports.com/college-football/scoreboard/FBS/2022/

In [4]:
game_ids = []
home_teams = []
away_teams = []
home_team_records = []
away_team_records = []
home_team_q4s = []
home_team_q3s = []
home_team_q2s = []
home_team_q1s = []
home_team_finals = []
home_team_halfs = []
away_team_q4s = []
away_team_q3s = []
away_team_q2s = []
away_team_q1s = []
away_team_finals = []
away_team_halfs = []
home_team_nicknames = []
away_team_nicknames = []
home_first_pos = []
for div in soup.find_all('div', class_=lambda x: x and x.startswith('single-score-card')):
    # get game_ids
    data_abbrev = div.get('data-abbrev')
    game_id = (data_abbrev)
    
    # find the table with the scores
    table = div.find('div', class_='in-progress-table section')
    #print(table)
    # get the team names
    home_team = (table.find_all('a', class_='team-name-link')[0].text.strip())
    away_team = (table.find_all('a', class_='team-name-link')[1].text.strip())
    
    # get the scores for each quarter
    game = ([td.text.strip() for td in table.find_all('td')])
    
    if len(game) == 12: # check if all game data is there
        # get the team's season record
        home_team_records.append(re.findall('\d\d?-\d\d?',game[0]))
        away_team_records.append(re.findall('\d\d?-\d\d?',game[6]))
        
        # get the quarter data and do some processing on it
        home_team_q1s.append(int(game[1]))
        home_team_q2s.append(int(game[2]))
        home_team_q3s.append(int(game[3]))
        home_team_q4s.append(int(game[4]))
        home_team_finals.append(int(game[5]))
        home_team_halfs.append(int(game[1]) + int(game[2]))
        away_team_q1s.append(int(game[7]))
        away_team_q2s.append(int(game[8]))
        away_team_q3s.append(int(game[9]))
        away_team_q4s.append(int(game[10]))
        away_team_finals.append(int(game[11]))
        away_team_halfs.append(int(game[7]) + int(game[8]))
        
        # append identifying variables to their lists
        game_ids.append(game_id)
        home_teams.append(home_team)
        away_teams.append(away_team)
        
        # check if there is a play by play page
        if div.find('div', class_='bottom-bar'):
            if 'Box Score' in div.find('div', class_='bottom-bar').text:
                pbp_url = f'https://www.cbssports.com/college-football/gametracker/playbyplay/{game_id}'
                pbp_page = requests.get(pbp_url)
                pbp_soup = bs(pbp_page.content)
                nicknames = pbp_soup.find_all('div',class_='nickname')
                home_team_nicknames.append(nicknames[0].text.strip())
                away_team_nicknames.append(nicknames[1].text.strip())
                first_pos = pbp_soup.find_all('span',class_='TeamName')[1].text.strip()
                if first_pos == nicknames[0].text.strip():
                    home_first_pos.append(1)
                else: home_first_pos.append(0)

                
        

Razorbacks Tigers Razorbacks
Eagles Huskies Huskies


KeyboardInterrupt: 

In [47]:
df = pd.DataFrame(data = {
    'year' : [year for i in range(len(game_ids))],
    'week' : [week for i in range(len(game_ids))],
    'game_id' : game_ids,
    'home_team' : home_teams,
    'away_team' : away_teams,
    'home_team_record' : home_team_records,
    'away_team_record' : away_team_records,
    'home_team_halftime' : home_team_halfs,
    'away_team_halftime' : away_team_halfs,
    'home_team_final' : home_team_finals,
    'away_team_final' : away_team_finals,
    'home_team_q1' : home_team_q1s,
    'home_team_q2' : home_team_q2s,
    'home_team_q3' : home_team_q3s,
    'home_team_q4' : home_team_q4s,
    'away_team_q1' : away_team_q1s,
    'away_team_q2' : away_team_q2s,
    'away_team_q3' : away_team_q3s,
    'away_team_q4' : away_team_q4s
    })

df['halftime_differential'] = df['home_team_halftime'] - df['away_team_halftime']
df['final_differential'] = df['home_team_final'] - df['away_team_final']

In [49]:
df[['halftime_differential','final_differential']].corr()

halftime_differential  final_differential
halftime_differential               1.000000            0.849791
final_differential                  0.849791            1.000000

All the data

In [12]:
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup as bs
import requests
import re

# initialize columns
game_ids = []
home_teams = []
away_teams = []
home_team_records = []
away_team_records = []
home_team_q4s = []
home_team_q3s = []
home_team_q2s = []
home_team_q1s = []
home_team_finals = []
home_team_halfs = []
away_team_q4s = []
away_team_q3s = []
away_team_q2s = []
away_team_q1s = []
away_team_finals = []
away_team_halfs = []
homewins_awaywins = []
years_list = []
weeks_list = []
home_team_nicknames = []
away_team_nicknames = []
home_first_pos = []

# define the range of years and weeks
years = range(2017, 2023)
weeks = range(1,16)

for year in years:
    for week in weeks:
        
        print(f'Getting week {week} of {year}')
        url = f'https://www.cbssports.com/college-football/scoreboard/FBS/{year}/regular/{week}/'
        
        # get page
        page = requests.get(url)
        soup = bs(page.content)
        
        
        
        for div in soup.find_all('div', class_=lambda x: x and x.startswith('single-score-card')):
            # get game_ids
            data_abbrev = div.get('data-abbrev')
            game_id = (data_abbrev)
            
            # find the table with the scores
            table = div.find('div', class_='in-progress-table section')
            #print(table)
            # get the team names
            home_team = (table.find_all('a', class_='team-name-link')[0].text.strip())
            away_team = (table.find_all('a', class_='team-name-link')[1].text.strip())
            
            # get the scores for each quarter
            game = ([td.text.strip() for td in table.find_all('td')])
            
            if len(game) == 12 and all(element != '-' for element in game): # check if all game data is there
                # get the quarter data and do some processing on it
                home_team_q1s.append(int(game[1]))
                home_team_q2s.append(int(game[2]))
                home_team_q3s.append(int(game[3]))
                home_team_q4s.append(int(game[4]))
                home_team_finals.append(int(game[5]))
                home_team_halfs.append(int(game[1]) + int(game[2]))
                away_team_q1s.append(int(game[7]))
                away_team_q2s.append(int(game[8]))
                away_team_q3s.append(int(game[9]))
                away_team_q4s.append(int(game[10]))
                away_team_finals.append(int(game[11]))
                away_team_halfs.append(int(game[7]) + int(game[8]))
                #homewins_awaywins.append(int(re.findall('\d\d?',game[0])[0]) - int(re.findall('\d\d?',game[6])[0]) if (re.search('\d\d?',game[0]) and re.search('\d\d?',game[6])) else pd.NA)
                
                # append identifying variables to their lists
                game_ids.append(game_id)
                home_teams.append(home_team)
                away_teams.append(away_team)
                years_list.append(year)
                weeks_list.append(week)
                
                # get the team's season record, in try blocks to handle when there is no record listed
                records = table.find_all('span',class_='record')
                
                try:home_team_records.append(records[0].text.strip())
                except:home_team_records.append(pd.NA)
                try:away_team_records.append(records[1].text.strip())
                except:away_team_records.append(pd.NA)
                try:homewins_awaywins.append(int(re.findall('\d\d?',records[0].text.strip())[0]) - int(re.findall('\d\d?',records[1].text.strip())[0]))
                except: homewins_awaywins.append(pd.NA)
                
                # check if there is a play by play page
                if div.find('div', class_='bottom-bar'):
                    if 'Box Score' in div.find('div', class_='bottom-bar').text:
                        pbp_url = f'https://www.cbssports.com/college-football/gametracker/playbyplay/{game_id}'
                        pbp_page = requests.get(pbp_url)
                        pbp_soup = bs(pbp_page.content)
                        nicknames = pbp_soup.find_all('div',class_='nickname')
                        home_team_nicknames.append(nicknames[0].text.strip())
                        away_team_nicknames.append(nicknames[1].text.strip())
                        first_pos = pbp_soup.find_all('span',class_='TeamName')[1].text.strip()
                        if first_pos == nicknames[0].text.strip():
                            home_first_pos.append(1)
                        else: home_first_pos.append(0)
                    else:
                        home_first_pos.append(pd.NA)
                        away_team_nicknames.append(pd.NA)
                        home_team_nicknames.append(pd.NA)
                else:
                    home_first_pos.append(pd.NA)
                    away_team_nicknames.append(pd.NA)
                    home_team_nicknames.append(pd.NA)

Getting week 1 of 2017
Getting week 2 of 2017
Getting week 3 of 2017
Getting week 4 of 2017
Getting week 5 of 2017
Getting week 6 of 2017
Getting week 7 of 2017
Getting week 8 of 2017
Getting week 9 of 2017
Getting week 10 of 2017
Getting week 11 of 2017
Getting week 12 of 2017
Getting week 13 of 2017
Getting week 14 of 2017
Getting week 15 of 2017
Getting week 1 of 2018
Getting week 2 of 2018
Getting week 3 of 2018
Getting week 4 of 2018
Getting week 5 of 2018
Getting week 6 of 2018
Getting week 7 of 2018
Getting week 8 of 2018
Getting week 9 of 2018
Getting week 10 of 2018
Getting week 11 of 2018
Getting week 12 of 2018
Getting week 13 of 2018
Getting week 14 of 2018
Getting week 15 of 2018
Getting week 1 of 2019
Getting week 2 of 2019
Getting week 3 of 2019
Getting week 4 of 2019
Getting week 5 of 2019
Getting week 6 of 2019
Getting week 7 of 2019
Getting week 8 of 2019
Getting week 9 of 2019
Getting week 10 of 2019
Getting week 11 of 2019
Getting week 12 of 2019
Getting week 13 of 

In [28]:
df = pd.DataFrame(data = {
    'year' : years_list,
    'week' : weeks_list,
    'game_id' : game_ids,
    'home_team' : home_teams,
    'home_team_nickname': home_team_nicknames,
    'away_team' : away_teams,
    'away_team_nickname': away_team_nicknames,
    'home_team_record' : home_team_records,
    'away_team_record' : away_team_records,
    'home_first_pos': home_first_pos,
    'home_team_halftime' : home_team_halfs,
    'away_team_halftime' : away_team_halfs,
    'home_team_final' : home_team_finals,
    'away_team_final' : away_team_finals,
    'home_team_q1' : home_team_q1s,
    'home_team_q2' : home_team_q2s,
    'home_team_q3' : home_team_q3s,
    'home_team_q4' : home_team_q4s,
    'away_team_q1' : away_team_q1s,
    'away_team_q2' : away_team_q2s,
    'away_team_q3' : away_team_q3s,
    'away_team_q4' : away_team_q4s,
    'homewins-awaywins': homewins_awaywins
    })

df['halftime_differential'] = df['home_team_halftime'] - df['away_team_halftime']
df['final_differential'] = df['home_team_final'] - df['away_team_final']
df.to_csv('cbsFootballData.csv',index=None)
print(df)

      year  week                       game_id      home_team  \
0     2017     1      NCAAF_20170903_TXAM@UCLA      Texas A&M   
1     2017     1     NCAAF_20170903_WVU@VATECH  West Virginia   
2     2017     1      NCAAF_20170902_AKRON@PSU          Akron   
3     2017     1     NCAAF_20170902_BALLST@ILL       Ball St.   
4     2017     1  NCAAF_20170902_BGREEN@MICHST  Bowling Green   
...    ...   ...                           ...            ...   
4481  2022    14       NCAAF_20221203_CLEM@UNC        Clemson   
4482  2022    14    NCAAF_20221203_PURDUE@MICH         Purdue   
4483  2022    14     NCAAF_20221202_AKRON@BUFF          Akron   
4484  2022    14    NCAAF_20221202_NTEXAS@TXSA    North Texas   
4485  2022    14       NCAAF_20221202_UTAH@USC           Utah   

     home_team_nickname       away_team away_team_nickname home_team_record  \
0                  <NA>            UCLA               <NA>              0-1   
1                  <NA>   Virginia Tech               <NA>   

In [247]:
df = pd.read_csv('cbsFootballData.csv')

In [30]:
print(df[['halftime_differential','homewins-awaywins','home_first_pos','final_differential']].dropna().corr(numeric_only=False))

                       halftime_differential  homewins-awaywins  \
halftime_differential               1.000000           0.535790   
homewins-awaywins                   0.535790           1.000000   
home_first_pos                      0.036494          -0.020551   
final_differential                  0.850494           0.628994   

                       home_first_pos  final_differential  
halftime_differential        0.036494            0.850494  
homewins-awaywins           -0.020551            0.628994  
home_first_pos               1.000000           -0.024055  
final_differential          -0.024055            1.000000  


In [34]:
df_lm = df[['halftime_differential','final_differential']]
df_lm.dropna(inplace=True)
df_lm['intercept'] = 1
exog = df_lm[['intercept', 'halftime_differential']]
endog = df_lm['final_differential']

# Fit the multivariate linear model
model = sm.OLS(endog, exog).fit()

# Get the regression coefficients
coefficients = model.params

# Print the results
print(model.summary())

                            OLS Regression Results                            
Dep. Variable:     final_differential   R-squared:                       0.721
Model:                            OLS   Adj. R-squared:                  0.721
Method:                 Least Squares   F-statistic:                 1.159e+04
Date:                Mon, 30 Oct 2023   Prob (F-statistic):               0.00
Time:                        09:39:49   Log-Likelihood:                -17550.
No. Observations:                4486   AIC:                         3.510e+04
Df Residuals:                    4484   BIC:                         3.512e+04
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
intercept                -1.43

C:\Users\conno\AppData\Local\Temp\ipykernel_25224\2360432786.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_lm.dropna(inplace=True)
C:\Users\conno\AppData\Local\Temp\ipykernel_25224\2360432786.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_lm['intercept'] = 1


In [31]:
df_lm = df[['halftime_differential','homewins-awaywins','final_differential']]
df_lm.dropna(inplace=True)
df_lm['intercept'] = 1
df_lm['homewins-awaywins'] = df_lm['homewins-awaywins'].astype(int)
#df_lm['interaction'] = df_lm['halftime_differential'] * df_lm['homewins-awaywins']
exog = df_lm[['intercept', 'halftime_differential', 'homewins-awaywins']]
endog = df_lm['final_differential']

# Fit the multivariate linear model
model = sm.OLS(endog, exog).fit()

# Get the regression coefficients
coefficients = model.params

# Print the results
print(model.summary())

C:\Users\conno\AppData\Local\Temp\ipykernel_25224\662732116.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_lm.dropna(inplace=True)
C:\Users\conno\AppData\Local\Temp\ipykernel_25224\662732116.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_lm['intercept'] = 1
C:\Users\conno\AppData\Local\Temp\ipykernel_25224\662732116.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stab

                            OLS Regression Results                            
Dep. Variable:     final_differential   R-squared:                       0.760
Model:                            OLS   Adj. R-squared:                  0.760
Method:                 Least Squares   F-statistic:                     7099.
Date:                Mon, 30 Oct 2023   Prob (F-statistic):               0.00
Time:                        09:38:13   Log-Likelihood:                -17200.
No. Observations:                4483   AIC:                         3.441e+04
Df Residuals:                    4480   BIC:                         3.443e+04
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
intercept                -1.66

With possesion factored in

In [32]:
df_lm = df[['halftime_differential','homewins-awaywins','home_first_pos','final_differential']]
df_lm.dropna(inplace=True)
df_lm['intercept'] = 1
df_lm['homewins-awaywins'] = df_lm['homewins-awaywins'].astype(int)
df_lm['home_first_pos'] = df_lm['home_first_pos'].astype(int)
#df_lm['interaction'] = df_lm['halftime_differential'] * df_lm['homewins-awaywins']
exog = df_lm[['intercept', 'halftime_differential', 'homewins-awaywins','home_first_pos']]
endog = df_lm['final_differential']

# Fit the multivariate linear model
model = sm.OLS(endog, exog).fit()

# Get the regression coefficients
coefficients = model.params

# Print the results
print(model.summary())

                            OLS Regression Results                            
Dep. Variable:     final_differential   R-squared:                       0.768
Model:                            OLS   Adj. R-squared:                  0.767
Method:                 Least Squares   F-statistic:                     3429.
Date:                Mon, 30 Oct 2023   Prob (F-statistic):               0.00
Time:                        09:38:23   Log-Likelihood:                -11908.
No. Observations:                3120   AIC:                         2.382e+04
Df Residuals:                    3116   BIC:                         2.385e+04
Df Model:                           3                                         
Covariance Type:            nonrobust                                         
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
intercept                -0.59

C:\Users\conno\AppData\Local\Temp\ipykernel_25224\472316338.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_lm.dropna(inplace=True)
C:\Users\conno\AppData\Local\Temp\ipykernel_25224\472316338.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_lm['intercept'] = 1
C:\Users\conno\AppData\Local\Temp\ipykernel_25224\472316338.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stab

Considering a team's average relative performance in second half and first half (spoiler, it doesn't help the model)

In [246]:
winners = []
losers = []
for index, row in df.iterrows():
    winners.append(row['home_team'] if row['final_differential'] > 0 else row['away_team'])
    losers.append(row['home_team'] if row['final_differential'] < 0 else row['away_team'])
df['winner'] = winners
df['loser'] = losers

df = df[df['home_team'].isin(df['winner']) & df['away_team'].isin(df['winner'])] 
teams = pd.concat([df['home_team'], df['away_team']]).unique()
teams_df = pd.DataFrame({'Team': sorted(teams)})
teams = teams_dict = {team: index for index, team in enumerate(teams_df['Team'])}

teams_num_games = teams.copy()
for key in teams_num_games:
    teams_num_games[key] = 0
teams_total_h1 = teams.copy()
for key in teams_total_h1:
    teams_total_h1[key] = 0
teams_total_h2 = teams.copy()
for key in teams_total_h2:
    teams_total_h2[key] = 0
    
    
for index, row in df.iterrows():
    teams_num_games[row['home_team']] += 1
    teams_total_h1[row['home_team']] += row['home_team_q1']+row['home_team_q2']
    teams_total_h2[row['home_team']] += row['home_team_q3']+row['home_team_q4']
    
    teams_num_games[row['away_team']] += 1
    teams_total_h1[row['away_team']] += row['away_team_q1']+row['away_team_q2']
    teams_total_h2[row['away_team']] += row['away_team_q3']+row['away_team_q4']
    
teams_h2h1_ratio = teams.copy()
for key in teams:
    teams_h2h1_ratio[key] =  (teams_total_h2[key] / teams_total_h1[key])
print(teams_h2h1_ratio['BYU'])
away_ratios = []
home_ratios = []
for index,row in df.iterrows():
    away_ratios.append(teams_h2h1_ratio[row['away_team']])
    home_ratios.append(teams_h2h1_ratio[row['home_team']])
    
df['home_h2h1_ratio'] = home_ratios
df['away_h2h1_ratio'] = away_ratios   
##! These ratios are avg(points scored in half2) / avg(points scored in half1) for a team.  If > 1, then they on average score more points in half 2


0.7675312199807877


C:\Users\conno\AppData\Local\Temp\ipykernel_25224\868323975.py:44: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['home_h2h1_ratio'] = home_ratios
C:\Users\conno\AppData\Local\Temp\ipykernel_25224\868323975.py:45: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['away_h2h1_ratio'] = away_ratios


In [168]:
df_lm = df[['halftime_differential','homewins-awaywins','home_first_pos','final_differential','home_h2h1_ratio','away_h2h1_ratio']]

df_lm.dropna(inplace=True)
df_lm['intercept'] = 1
df_lm['homewins-awaywins'] = df_lm['homewins-awaywins'].astype(int)
df_lm['home_first_pos'] = df_lm['home_first_pos'].astype(int)
df_lm['interaction_term'] = df_lm['home_h2h1_ratio'] * df_lm['away_h2h1_ratio']
#df_lm['interaction'] = df_lm['halftime_differential'] * df_lm['homewins-awaywins']
exog = df_lm[['intercept', 'halftime_differential', 'homewins-awaywins','home_first_pos','home_h2h1_ratio','away_h2h1_ratio','interaction_term']]
endog = df_lm['final_differential']

# Fit the multivariate linear model
model = sm.OLS(endog, exog).fit()

# Get the regression coefficients
coefficients = model.params

# Print the results
print(model.summary())

                            OLS Regression Results                            
Dep. Variable:     final_differential   R-squared:                       0.757
Model:                            OLS   Adj. R-squared:                  0.757
Method:                 Least Squares   F-statistic:                     1503.
Date:                Tue, 31 Oct 2023   Prob (F-statistic):               0.00
Time:                        22:21:42   Log-Likelihood:                -10993.
No. Observations:                2897   AIC:                         2.200e+04
Df Residuals:                    2890   BIC:                         2.204e+04
Df Model:                           6                                         
Covariance Type:            nonrobust                                         
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
intercept                 8.96

C:\Users\conno\AppData\Local\Temp\ipykernel_25224\399732118.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_lm.dropna(inplace=True)
C:\Users\conno\AppData\Local\Temp\ipykernel_25224\399732118.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_lm['intercept'] = 1
C:\Users\conno\AppData\Local\Temp\ipykernel_25224\399732118.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stab

Doing Bradley Terry Model

In [256]:
winners = []
losers = []
for index, row in df.iterrows():
    winners.append(row['home_team'] if row['final_differential'] > 0 else row['away_team'])
    losers.append(row['home_team'] if row['final_differential'] < 0 else row['away_team'])
df['winner'] = winners
df['loser'] = losers

In [102]:
df = df[df['home_team'].isin(df['winner']) & df['away_team'].isin(df['winner'])]
teams = pd.concat([df['home_team'], df['away_team']]).unique()
teams_df = pd.DataFrame({'Team': sorted(teams)})
teams = teams_dict = {team: index for index, team in enumerate(teams_df['Team'])}
teams

{'Air Force': 0,
 'Akron': 1,
 'Alabama': 2,
 'App. St.': 3,
 'Arizona': 4,
 'Arizona St.': 5,
 'Arkansas': 6,
 'Arkansas St.': 7,
 'Army': 8,
 'Auburn': 9,
 'BYU': 10,
 'Ball St.': 11,
 'Baylor': 12,
 'Boise St.': 13,
 'Boston College': 14,
 'Bowling Green': 15,
 'Buffalo': 16,
 'C. Carolina': 17,
 'C. Michigan': 18,
 'California': 19,
 'Cent. Ark.': 20,
 'Charlotte': 21,
 'Cincinnati': 22,
 'Clemson': 23,
 'Colorado': 24,
 'Colorado St.': 25,
 'Delaware': 26,
 'Duke': 27,
 'Duquesne': 28,
 'E. Michigan': 29,
 'ETSU': 30,
 'East Carolina': 31,
 'FAU': 32,
 'FIU': 33,
 'Florida': 34,
 'Florida State': 35,
 'Fresno St.': 36,
 'Ga. Southern': 37,
 'Georgia': 38,
 'Georgia St.': 39,
 'Georgia Tech': 40,
 'Hawaii': 41,
 'Holy Cross': 42,
 'Houston': 43,
 'Howard': 44,
 'Idaho': 45,
 'Idaho State': 46,
 'Illinois': 47,
 'Illinois St.': 48,
 'Incarnate Word': 49,
 'Indiana': 50,
 'Iowa': 51,
 'Iowa St.': 52,
 'Jacksonville St.': 53,
 'James Madison': 54,
 'Kansas': 55,
 'Kansas State': 56,
 

In [104]:
N = len(df)
X = np.zeros((N,len(teams)+1))
Y = np.zeros((N,1))
gameNumber = 0

for index, row in df.iterrows():
    home = row['home_team']
    away = row['away_team']
    # set winning team to 1 and losing team to -1
    X[gameNumber][teams[home]] = 1
    X[gameNumber][teams[away]] = -1
    Y[gameNumber] = 1
    X[gameNumber][len(teams)] = 1
    gameNumber += 1

In [124]:
X = np.matrix(X)
Xt = np.matrix.transpose(X)
XXt = np.dot(X,Xt)
Y = np.matrix(Y)
rankings = np.matrix(np.random.rand(len(teams)+1,1))
tol = 1.

cutoff = .001

while tol > cutoff:
    p = np.exp(np.dot(X,rankings)) / (1 + np.exp(np.dot(X,rankings)))
    gradient = np.matrix(np.zeros((1,len(teams)+1)))
    hessian = 0.
    for i in range(N):
        gradient += np.multiply(X[i],Y[i]) - np.multiply(X[i],p[i])
        hessian += XXt.item((i,i))*p[i]*(1-p[i])
    
    if hessian == 0: break # getting errors when the hessian becomes so small
    
    oldrankings = np.matrix.transpose(rankings)
    rankings = oldrankings + (1/hessian)*gradient

    tol = np.dot(rankings-oldrankings,np.matrix.transpose(rankings-oldrankings))

    rankings = np.matrix.transpose(rankings)


Glickman and Stern method

In [258]:
df = pd.read_csv('cbsFootballData.csv')

teams = pd.concat([df['home_team'], df['away_team']]).unique()
teams_df = pd.DataFrame({'Team': sorted(teams)})
teams = {team: index for index, team in enumerate(teams_df['Team'])}
teams

{'Abil Christian': 0,
 'Air Force': 1,
 'Akron': 2,
 'Alabama': 3,
 'Alabama A&M': 4,
 'Alabama St.': 5,
 'Albany': 6,
 'Alcorn St.': 7,
 'App. St.': 8,
 'Arizona': 9,
 'Arizona St.': 10,
 'Ark.-Pine Bluff': 11,
 'Arkansas': 12,
 'Arkansas St.': 13,
 'Army': 14,
 'Auburn': 15,
 'Austin Peay': 16,
 'BYU': 17,
 'Ball St.': 18,
 'Baylor': 19,
 'Bethune-Cook.': 20,
 'Boise St.': 21,
 'Boston College': 22,
 'Bowling Green': 23,
 'Bryant': 24,
 'Bucknell': 25,
 'Buffalo': 26,
 'C. Carolina': 27,
 'C. Michigan': 28,
 'CCSU': 29,
 'Cal-Poly': 30,
 'California': 31,
 'Campbell': 32,
 'Cent. Ark.': 33,
 'Charleston So.': 34,
 'Charlotte': 35,
 'Chattanooga': 36,
 'Cincinnati': 37,
 'Clemson': 38,
 'Colgate': 39,
 'Colorado': 40,
 'Colorado St.': 41,
 'Delaware': 42,
 'Delaware St.': 43,
 'Drake': 44,
 'Duke': 45,
 'Duquesne': 46,
 'E. Illinois': 47,
 'E. Kentucky': 48,
 'E. Michigan': 49,
 'E. Washington': 50,
 'ETSU': 51,
 'East Carolina': 52,
 'Elon': 53,
 'FAU': 54,
 'FIU': 55,
 'Florida': 56

In [260]:
n = len(df)
X = np.zeros((n,len(teams)))
Y = np.zeros((n,1))
gameNumber = 0

for index, row in df.iterrows():
    home = row['home_team']
    away = row['away_team']
    # set winning team to 1 and losing team to -1
    X[gameNumber][teams[home]] = 1
    X[gameNumber][teams[away]] = -1
    Y[gameNumber] = row['final_differential']
    gameNumber += 1

top = np.eye(len(teams)-1,len(teams)-1)
bottom = np.zeros((1,len(teams)-1))
W = np.vstack((top,bottom))

In [261]:
Xstar = np.matmul(X,W)

thetahatj = np.linalg.inv(np.matmul(np.transpose(Xstar),Xstar))@np.matmul(Xstar.T,Y)
thetas = np.matmul(W,thetahatj)

variance = (1/(len(df)-len(teams)-1))*np.transpose((Y-np.dot(X,thetas)))@(Y-np.dot(X,thetas))

In [264]:
from scipy.stats import norm

mean = thetas[teams['West Virginia']] - thetas[teams['BYU']]
sd = np.sqrt(variance)
print(1-norm.cdf(0,loc=mean,scale=sd))
print(mean)

[[0.63587704]]
[5.888233]


In [272]:
from scipy.stats import norm

home_win_prob = []
expected_diff = []
for index,row in df.iterrows():
    if row['year'] > 2017:break
    home_win_prob.append(pd.NA)
    expected_diff.append(pd.NA)

for year in range(2018,2023):
    for week in range(1,16):
        print(year,week)
        
        # Create a boolean mask for rows before the target year/week
        mask = (df['year'] < year) | ((df['year'] == year) & (df['week'] < week))

        # Apply the mask to get the filtered DataFrame
        filtered_df = df[mask]
        
        # get the teams
        teams = pd.concat([filtered_df['home_team'], filtered_df['away_team']]).unique()
        teams_df = pd.DataFrame({'Team': sorted(teams)})
        teams = {team: index for index, team in enumerate(teams_df['Team'])}
        
        # Regression to get Theta values
        n = len(filtered_df)
        X = np.zeros((n,len(teams)))
        Y = np.zeros((n,1))
        

        for index, row in filtered_df.iterrows():
            home = row['home_team']
            away = row['away_team']
            # set winning team to 1 and losing team to -1
            X[index][teams[home]] = 1
            X[index][teams[away]] = -1
            Y[index] = row['final_differential']

        top = np.eye(len(teams)-1,len(teams)-1)
        bottom = np.zeros((1,len(teams)-1))
        W = np.vstack((top,bottom))
        Xstar = np.matmul(X,W)

        thetahat = np.matmul(W,np.linalg.inv(np.matmul(np.transpose(Xstar),Xstar))@np.matmul(Xstar.T,Y))
        variance = (1/(len(filtered_df)-len(teams)-1))*np.transpose((Y-np.dot(X,thetahat)))@(Y-np.dot(X,thetahat))
        sd = np.sqrt(variance)
        
        # Create a boolean mask for rows before the target year/week
        mask = ((df['year'] == year) & (df['week'] == week))

        # Apply the mask to get the filtered DataFrame
        filtered_df2 = df[mask]
        for index,row in filtered_df2.iterrows():
            
            try: 
                mean = thetahat[teams[row['home_team']]] - thetahat[teams[row['away_team']]]
                home_win_prob.append(1-norm.cdf(0,loc=mean,scale=sd).item())
                expected_diff.append(mean.item())
            except:
                home_win_prob.append(pd.NA)
                expected_diff.append(pd.NA)
df['home_win_prob'] = home_win_prob
df['predicted_diff'] = expected_diff



2018 1
2018 2
2018 3
2018 4
2018 5
2018 6
2018 7
2018 8
2018 9
2018 10
2018 11
2018 12
2018 13
2018 14
2018 15
2019 1
2019 2
2019 3
2019 4
2019 5
2019 6
2019 7
2019 8
2019 9
2019 10
2019 11
2019 12
2019 13
2019 14
2019 15
2020 1
2020 2
2020 3
2020 4
2020 5
2020 6
2020 7
2020 8
2020 9
2020 10
2020 11
2020 12
2020 13
2020 14
2020 15
2021 1
2021 2
2021 3
2021 4
2021 5
2021 6
2021 7
2021 8
2021 9
2021 10
2021 11
2021 12
2021 13
2021 14
2021 15
2022 1
2022 2
2022 3
2022 4
2022 5
2022 6
2022 7
2022 8
2022 9
2022 10
2022 11
2022 12
2022 13
2022 14
2022 15


In [270]:

df_lm = df[['halftime_differential','homewins-awaywins','home_first_pos','home_win_prob','predicted_diff','final_differential']]
df_lm.dropna(inplace=True)
df_lm['intercept'] = 1
df_lm['homewins-awaywins'] = df_lm['homewins-awaywins'].astype(int)
df_lm['home_first_pos'] = df_lm['home_first_pos'].astype(int)
df_lm['home_win_prob'] = df_lm['home_win_prob'].astype(float)
df_lm['predicted_diff'] = df_lm['predicted_diff'].astype(float)
exog = df_lm[['intercept', 'halftime_differential', 'homewins-awaywins','home_first_pos','home_win_prob']]
endog = df_lm['final_differential']

# Fit the multivariate linear model
model = sm.OLS(endog, exog).fit()

# Get the regression coefficients
coefficients = model.params

# Print the results
print(model.summary())

                            OLS Regression Results                            
Dep. Variable:     final_differential   R-squared:                       0.779
Model:                            OLS   Adj. R-squared:                  0.779
Method:                 Least Squares   F-statistic:                     2727.
Date:                Sat, 04 Nov 2023   Prob (F-statistic):               0.00
Time:                        09:52:32   Log-Likelihood:                -11762.
No. Observations:                3102   AIC:                         2.353e+04
Df Residuals:                    3097   BIC:                         2.356e+04
Df Model:                           4                                         
Covariance Type:            nonrobust                                         
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
intercept                -5.86

C:\Users\conno\AppData\Local\Temp\ipykernel_25224\483385457.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_lm.dropna(inplace=True)
C:\Users\conno\AppData\Local\Temp\ipykernel_25224\483385457.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_lm['intercept'] = 1
C:\Users\conno\AppData\Local\Temp\ipykernel_25224\483385457.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stab

In [59]:
# recalculating win probability based on only the last 15 weeks of football
home_win_prob = []
expected_diff = []
for index,row in df.iterrows():
    if row['year'] > 2017:break # don't predict for the 2017 season
    home_win_prob.append(pd.NA)
    expected_diff.append(pd.NA)

for year in range(2018,2023):
    for week in range(1,16):
        print(year,week)
        
        # Create a boolean mask for the last 15 weeks before this week
        mask = ((df['year'] == year-1) & (df['week'] >= week)) | ((df['year'] == year) & (df['week'] < week))

        # Apply the mask to get the filtered DataFrame
        filtered_df = df[mask]
        
        # get the teams
        teams = pd.concat([filtered_df['home_team'], filtered_df['away_team']]).unique()
        teams_df = pd.DataFrame({'Team': sorted(teams)})
        teams = {team: index for index, team in enumerate(teams_df['Team'])}
        
        # Regression to get Theta values
        n = len(filtered_df)
        X = np.zeros((n,len(teams)))
        Y = np.zeros((n,1))
        
        i = 0
        for index,row in filtered_df.iterrows():
            home = row['home_team']
            away = row['away_team']
            # set winning team to 1 and losing team to -1
            X[i][teams[home]] = 1
            X[i][teams[away]] = -1
            Y[i] = row['final_differential']
            i += 1

        top = np.eye(len(teams)-1,len(teams)-1)
        bottom = np.zeros((1,len(teams)-1))
        W = np.vstack((top,bottom))
        Xstar = np.matmul(X,W)

        thetahat = np.matmul(W,np.linalg.inv(np.matmul(np.transpose(Xstar),Xstar))@np.matmul(Xstar.T,Y))
        variance = (1/(len(filtered_df)-len(teams)-1))*np.transpose((Y-np.dot(X,thetahat)))@(Y-np.dot(X,thetahat))
        sd = np.sqrt(variance)
        
        # Create a boolean mask for rows before the target year/week
        mask = ((df['year'] == year) & (df['week'] == week))
        # Apply the mask to get the filtered DataFrame
        filtered_df2 = df[mask]
        team_counts = pd.concat([filtered_df['home_team'], filtered_df['away_team']]).value_counts()
        for index,row in filtered_df2.iterrows():
            try: 
                #make sure both teams have played at least 7 games in the last 15 (trying to avoid problems with not enough samples)
                if team_counts[row['home_team']] > 10 and team_counts[row['away_team']] > 10:
                    mean = thetahat[teams[row['home_team']]] - thetahat[teams[row['away_team']]]
                    home_win_prob.append(1-norm.cdf(0,loc=mean,scale=sd).item())
                    expected_diff.append(mean.item())
                else:
                    home_win_prob.append(pd.NA)
                    expected_diff.append(pd.NA)
            except:
                home_win_prob.append(pd.NA)
                expected_diff.append(pd.NA)


df['home_win_prob_last15'] = home_win_prob
df['predicted_diff_last15'] = expected_diff

2018 1
2018 2
2018 3
2018 4
2018 5
2018 6
2018 7
2018 8
2018 9
2018 10
2018 11
2018 12
2018 13
2018 14
2018 15
2019 1
2019 2
2019 3
2019 4
2019 5
2019 6
2019 7
2019 8
2019 9
2019 10
2019 11
2019 12
2019 13
2019 14
2019 15
2020 1
2020 2
2020 3
2020 4
2020 5
2020 6
2020 7
2020 8
2020 9
2020 10
2020 11
2020 12
2020 13
2020 14
2020 15
2021 1
2021 2
2021 3
2021 4
2021 5
2021 6
2021 7
2021 8
2021 9
2021 10
2021 11
2021 12
2021 13
2021 14
2021 15
2022 1
2022 2
2022 3
2022 4
2022 5
2022 6
2022 7
2022 8
2022 9
2022 10
2022 11
2022 12
2022 13
2022 14
2022 15


In [4]:
df.drop(columns=['home_win_prob_last15_2','predicted_diff_last15_2']).to_csv('cbsFootballData.csv')